In [ ]:
!pip install --upgrade pinecone-client tqdm
!pip install tensorflow tensorflow-hub transformers
!pip install rouge-score
!pip install bert-score
!pip install moverscore
!pip install pyemd
!pip install transformers torch numpy
!pip3 uninstall --yes torch torchaudio torchvision
!pip3 install torch torchaudio torchvision


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 244.8/244.8 kB 16.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 117.6/117.6 kB 9.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for rouge-score: filename=rouge_score-0.1.2-py3-none-any.whl size=24935 sha256=e4794c637235e60f1c9e055168b440acf2a4e1359ad4072636c8e60bfba6640d
  Stored in directory: /root/.cache/pip/wheels/5f/dd/89/461065a73be61a532ff8599a28e9beef17985c9e9c31e541b4
Successfully built rouge-score
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cufft

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 662.6/662.6 kB 38.3 MB/s eta 0:00:00
Found existing installation: torch 2.3.1+cu121
Uninstalling torch-2.3.1+cu121:
  Successfully uninstalled torch-2.3.1+cu121
Found existing installation: torchaudio 2.3.1+cu121
Uninstalling torchaudio-2.3.1+cu121:
  Successfully uninstalled torchaudio-2.3.1+cu121
Found existing installation: torchvision 0.18.1+cu121
Uninstalling torchvision-0.18.1+cu121:
  Successfully uninstalled torchvision-0.18.1+cu121
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 797.2/797.2 MB 1.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 1.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 209.4/209.4 MB 10.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.4/3.4 MB 93.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.0/7.0 MB 117.3 MB/s eta 0:00:00
  Attempting uninstall: triton
    Found existing installation: triton 2.3.1
    Uninstalling triton-2.3.1:
      S

In [ ]:
# Import necessary libraries
import json
import pandas as pd
import numpy as np
import tensorflow as tf
import tensorflow_hub as hub
from pinecone import Pinecone, ServerlessSpec
from transformers import T5ForConditionalGeneration, T5Tokenizer, BertTokenizer, BertModel
from transformers import BartTokenizer, BartForConditionalGeneration
import torch
import numpy as np
from pyemd import emd
import random
from rouge_score import rouge_scorer
from bert_score import score as bert_score
from collections import defaultdict
from nltk.translate import meteor_score
import nltk
import re
import os
from moverscore_v2 import get_idf_dict, word_mover_score
import gc
from collections import defaultdict

/usr/local/lib/python3.10/dist-packages/transformers/deepspeed.py:24: FutureWarning: transformers.deepspeed module is deprecated and will be removed in a future version. Please import deepspeed modules directly from transformers.integrations
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
GroupViT models are not usable since `tensorflow_probability` can't be loaded. It seems you have `tensorflow_probability` installed with the wrong tensorflow version.Please try to reinstall it following the instructions he

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
import re
import json
from wordcloud import WordCloud
import matplotlib.pyplot as plt
from collections import Counter

In [ ]:
nltk.download('wordnet')

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

**Data and Text Embedding**

In [ ]:


#Function to remove special characters and clean the text
def clean_text(text):
    text = text.lower()  # Convert text to lowercase
    text = re.sub(r'={2,}', '', text)  # Remove specific sequences like ===
    text = re.sub(r'[^a-z0-9\s]+', '', text)  # Remove other special characters
    text = re.sub(r'\s+', ' ', text)  # Replace multiple spaces with a single space
    text = text.strip()  # Trim leading and trailing spaces
    return text

# Function to load data from a file
def load_data(file_path):
    with open(file_path, 'r', encoding='utf-8') as f:
        lines = f.readlines()
        data = [json.loads(line) for line in lines]
    return data

# Load train and test data
train_file_path = '/content/drive/MyDrive/Wiki-Hades/Wiki-Hades/train.txt'
test_file_path = '/content/drive/MyDrive/Wiki-Hades/Wiki-Hades/test.txt'

train_data = load_data(train_file_path)[:100]  # Use first 100 rows of train data
test_data = load_data(test_file_path)[:10]  # Use first 10 rows of test data

# Clean the train and test texts
cleaned_train_texts = [clean_text(entry['replaced']) for entry in train_data]
cleaned_test_texts = [clean_text(entry['replaced']) for entry in test_data]

In [ ]:
 #Initialize Universal Sentence Encoder for embeddings
use_model = hub.load("https://tfhub.dev/google/universal-sentence-encoder/4")

# Generate embeddings for cleaned_train_texts
train_embeddings = use_model(cleaned_train_texts).numpy()

# Generate embeddings for cleaned_test_texts
test_embeddings = use_model(cleaned_test_texts).numpy()

In [ ]:
# Pinecone initialization
api_key = "869aa034-b0ee-4397-b713-4873ef889335"
environment = "us-east1-gcp"
index_name = "quickstart"

pc = Pinecone(api_key=api_key)

# Create index if it doesn't exist
if index_name not in [index['name'] for index in pc.list_indexes()]:
    pc.create_index(
        name=index_name,
        dimension=512,
        metric="cosine",
        spec=ServerlessSpec(
            cloud="gcp",
            region=environment
        )
    )
index = pc.Index(index_name)

# Store embeddings in Pinecone with metadata
for i, embedding in enumerate(train_embeddings):
    metadata = {"text": cleaned_train_texts[i]}
    index.upsert(vectors=[{"id": str(i), "values": embedding.tolist(), "metadata": metadata}])

for i, embedding in enumerate(test_embeddings):
    metadata = {"text": cleaned_test_texts[i]}
    index.upsert(vectors=[{"id": str(i), "values": embedding.tolist(), "metadata": metadata}])

print("Embeddings stored in Pinecone with metadata.")

Embeddings stored in Pinecone with metadata.


In [ ]:
# Retrieve relevant texts for cleaned_test_texts
test_retrieved_texts = []
for i in range(len(cleaned_test_texts)):
    query_embedding = test_embeddings[i]  # quering test_embeddings for correspondence to cleaned_test_texts
    query_results = index.query(vector=query_embedding.tolist(), top_k=5, include_metadata=True)
    retrieved = [match['metadata']['text'] for match in query_results['matches'] if 'metadata' in match]
    test_retrieved_texts.append(retrieved)

# Retrieve relevant texts for cleaned_train_texts
train_retrieved_texts = []
for i in range(len(cleaned_train_texts)):
    query_embedding = train_embeddings[i]  # quering train_embeddings for correspondence to cleaned_train_texts
    query_results = index.query(vector=query_embedding.tolist(), top_k=5, include_metadata=True)
    retrieved = [match['metadata']['text'] for match in query_results['matches'] if 'metadata' in match]
    train_retrieved_texts.append(retrieved)

In [ ]:


# Function to inject random facts into the source text
def inject_random_facts(text, facts, num_facts=3):
    sentences = text.split('.')
    for _ in range(num_facts):
        fact = random.choice(facts)
        insert_position = random.randint(0, len(sentences) - 1)
        sentences.insert(insert_position, fact)
    text_with_facts = '. '.join(sentences)
    return text_with_facts

random_facts = [
    "Hades is the god of the underworld in Greek mythology",
    "Hades is often depicted with a helmet of invisibility",
    "Cerberus is Hades' three-headed guard dog",
    "Hades' realm is called the Underworld or Hades itself",
    "Persephone, Hades' wife, spends half the year in the Underworld",
    "Hades is one of the three brothers who divided the world",
    "Hades rarely leaves his dark realm",
    "The river Styx forms the boundary between Earth and the Underworld",
    "Hades has a cap of invisibility given to him by the Cyclopes",
    "Hades was both feared and respected by the ancient Greeks"
]

# Inject random facts into each text entry in the train and test datasets
injected_train_texts = [inject_random_facts(entry['replaced'], random_facts, num_facts=3) for entry in train_data]
injected_test_texts = [inject_random_facts(entry['replaced'], random_facts, num_facts=3) for entry in test_data]

# Clean the injected texts
cleaned_injected_train_texts = [clean_text(text) for text in injected_train_texts]
cleaned_injected_test_texts = [clean_text(text) for text in injected_test_texts]

**RAG Implementation with BART at temp 0.7**

In [ ]:


# Set up the device
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')


# Load BART tokenizer and model
tokenizer = BartTokenizer.from_pretrained('facebook/bart-large')
model = BartForConditionalGeneration.from_pretrained('facebook/bart-large').to(device)

# Set the number of epochs
num_epochs = 5
train_losses = []

# Training loop with adjustable epochs
optimizer = torch.optim.Adam(model.parameters(), lr=5e-5)

for epoch in range(num_epochs):
    print(f"Epoch {epoch + 1}/{num_epochs}")

    model.train()
    epoch_train_loss = 0

    for i in range(0, len(cleaned_injected_train_texts), 4):  # Batch size of 4
        batch_texts = cleaned_injected_train_texts[i:i+4]
        batch_retrieved_texts = train_retrieved_texts[i:i+4]
        input_texts = [f"Perform abstractive summarization: {text}" for text in batch_texts]

        # Check if input_texts is empty
        if not input_texts:
            raise ValueError("Input texts are empty.")

        # Print input texts for debugging
        print("Input texts:", input_texts)

        inputs = tokenizer(input_texts, return_tensors='pt', padding=True, truncation=True, max_length=512).to(device)
        label_max_length = int(0.5 * inputs['input_ids'].size(1))
        labels = tokenizer(batch_texts, return_tensors='pt', padding=True, truncation=True, max_length=label_max_length)['input_ids'].to(device)

        outputs = model(input_ids=inputs['input_ids'], attention_mask=inputs['attention_mask'], labels=labels)
        loss = outputs.loss

        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        epoch_train_loss += loss.item()

    avg_train_loss = epoch_train_loss / len(cleaned_injected_train_texts)
    train_losses.append(avg_train_loss)
    print(f"Training Loss: {avg_train_loss:.3f}")

    gc.collect()
    torch.cuda.empty_cache()

loading file vocab.json from cache at /root/.cache/huggingface/hub/models--facebook--bart-large/snapshots/cb48c1365bd826bd521f650dc2e0940aee54720c/vocab.json
loading file merges.txt from cache at /root/.cache/huggingface/hub/models--facebook--bart-large/snapshots/cb48c1365bd826bd521f650dc2e0940aee54720c/merges.txt
loading file added_tokens.json from cache at None
loading file special_tokens_map.json from cache at None
loading file tokenizer_config.json from cache at /root/.cache/huggingface/hub/models--facebook--bart-large/snapshots/cb48c1365bd826bd521f650dc2e0940aee54720c/tokenizer_config.json
loading file tokenizer.json from cache at /root/.cache/huggingface/hub/models--facebook--bart-large/snapshots/cb48c1365bd826bd521f650dc2e0940aee54720c/tokenizer.json
loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--facebook--bart-large/snapshots/cb48c1365bd826bd521f650dc2e0940aee54720c/config.json
Model config BartConfig {
  "_name_or_path": "facebook/bar

Epoch 1/5
Input texts: ['Perform abstractive summarization: christopher atkinson c 1738 23 april 1819 known as christopher atkinson savile or saville from about 1798 was an english merchant and politician the river styx forms the boundary between earth and the underworld born in yorkshire he moved to dorset and married the niece of a wealthy merchant entering that business himself he was elected at the 1780 general election as one of the two members of parliament mps for dorset west however he was expelled from the house of commons on the second sitting after being convicted of receiving a bribe and sentenced to detention in the pillory he was granted a royal warrant in 1791 and returned to parliament for the area in 1796 retaining the seat until he stood down at the 1802 general election he had changed his name to atkinson atkinson some time after 1793 hades realm is called the underworld or hades itself he then purchased extensive estates in westerleigh in hampshire which gave him co

In [ ]:


def complete_last_sentence(text):
    sentences = re.split('(?<=[.!?]) +', text)
    if len(sentences) > 1:
        if len(sentences[-1].split()) < 3:
            text = ' '.join(sentences[:-1])
        else:
            if not sentences[-1][-1] in '.!?':
                text = text + '.'
    else:
        if not text[-1] in '.!?':
            text = text + '.'
    return text

def generate_summary(text, retrieved_texts, model, tokenizer):
    text = complete_last_sentence(text)
    input_text = f"Refine the following summary using this additional context. Text: {text} Additional context: {' '.join(retrieved_texts)}"
    inputs = tokenizer.encode(input_text, return_tensors='pt', max_length=512, truncation=True).to(device)

    decoder_settings = {
        "no_repeat_ngram_size": 2,
        "max_length": int(0.5 * inputs.size(1)),
        "min_length": int(0.25 * inputs.size(1)),
        "length_penalty": 2.5,
        "temperature": 0.7,
        "top_p": 0.9,
        "top_k": 50,
        "num_beams": 5,
        "do_sample": True,
        "early_stopping": True
    }

    summary_ids = model.generate(inputs, **decoder_settings)
    final_summary = tokenizer.decode(summary_ids[0], skip_special_tokens=True)

    if not final_summary.endswith('.'):
        final_summary += '.'

    return final_summary

In [ ]:
# Initialize BERT model for evaluation
bert_tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
bert_model = BertModel.from_pretrained('bert-base-uncased')
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
bert_model.to(device)

def bert_encode(model, x, device='cpu'):
    model.eval()
    with torch.no_grad():
        x = [bert_tokenizer.encode(sent, add_special_tokens=True) for sent in x]
        x = torch.tensor(x).to(device)
        outputs = model(x)
        return outputs.last_hidden_state

loading file vocab.txt from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/vocab.txt
loading file added_tokens.json from cache at None
loading file special_tokens_map.json from cache at None
loading file tokenizer_config.json from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/tokenizer_config.json
loading file tokenizer.json from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/tokenizer.json
loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/config.json
Model config BertConfig {
  "_name_or_path": "bert-base-uncased",
  "architectures": [
    "BertForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "classifier_dropout": null,
  "gradient_checkpointing": false,
  "hidden_ac

In [ ]:




def word_mover_score(references, hypotheses, idf_dict_ref, idf_dict_hyp, stop_words=None, n_gram=1, remove_subwords=True):
    if stop_words is None:
        stop_words = []

    ref_embedding = bert_encode(bert_model.to(device), references, device)
    hyp_embedding = bert_encode(bert_model.to(device), hypotheses, device)

    ref_embedding = ref_embedding.cpu().numpy()
    hyp_embedding = hyp_embedding.cpu().numpy()

    scores = []
    for i in range(len(references)):
        ref_tokens = references[i].split()
        hyp_tokens = hypotheses[i].split()

        ref_idf = [idf_dict_ref[token] for token in ref_tokens if token not in stop_words]
        hyp_idf = [idf_dict_hyp[token] for token in hyp_tokens if token not in stop_words]

        ref_embedding_i = ref_embedding[i]
        hyp_embedding_i = hyp_embedding[i]

        max_len = max(len(ref_embedding_i), len(hyp_embedding_i))
        if len(ref_embedding_i) < max_len:
            ref_embedding_i = np.pad(ref_embedding_i, ((0, max_len - len(ref_embedding_i)), (0, 0)), mode='constant')
        if len(hyp_embedding_i) < max_len:
            hyp_embedding_i = np.pad(hyp_embedding_i, ((0, max_len - len(hyp_embedding_i)), (0, 0)), mode='constant')

        distance_matrix = np.zeros((max_len, max_len))
        for i in range(max_len):
            for j in range(max_len):
                distance_matrix[i][j] = np.linalg.norm(ref_embedding_i[i] - hyp_embedding_i[j])

        max_tokens = max(len(ref_idf), len(hyp_idf))
        ref_idf = np.pad(np.array(ref_idf), (0, max_tokens - len(ref_idf)))
        hyp_idf = np.pad(np.array(hyp_idf), (0, max_tokens - len(hyp_idf)))

        ref_idf = ref_idf / np.sum(ref_idf)
        hyp_idf = hyp_idf / np.sum(hyp_idf)

        score = emd(ref_idf, hyp_idf, distance_matrix)
        scores.append(1 / (1 + score))

    return scores

In [ ]:


# Evaluation metrics
def calculate_metrics(reference, hypothesis):
    rouge = rouge_scorer.RougeScorer(['rouge1', 'rouge2', 'rougeL'], use_stemmer=True)
    rouge_scores = rouge.score(reference, hypothesis)

    bert_precision, bert_recall, bert_f1 = bert_score([hypothesis], [reference], lang="en")

    meteor = meteor_score.meteor_score([reference.split()], hypothesis.split())

    idf_dict_ref = get_idf_dict([reference])
    idf_dict_hyp = get_idf_dict([hypothesis])
    moverscore_value = word_mover_score([reference], [hypothesis], idf_dict_ref, idf_dict_hyp)

    return {
        'ROUGE-1': rouge_scores['rouge1'].fmeasure,
        'ROUGE-2': rouge_scores['rouge2'].fmeasure,
        'ROUGE-L': rouge_scores['rougeL'].fmeasure,
        'METEOR': meteor,
        'BERTScore': bert_f1.item(),
        'Precision': bert_precision.item(),
        'Recall': bert_recall.item(),
        'MoverScore': moverscore_value[0]
    }


In [ ]:
# Move the model to the correct device
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model.to(device)

# Set batch size
batch_size = 8

# Generate summaries for the training dataset using batch processing
train_summaries = []

for i in range(0, len(cleaned_injected_train_texts), batch_size):
    batch_texts = cleaned_injected_train_texts[i:i + batch_size]
    batch_retrieved_texts = train_retrieved_texts[i:i + batch_size]

    # Generate summaries for the current batch
    batch_summaries = [generate_summary(text, retrieved_text, model, tokenizer)
                       for text, retrieved_text in zip(batch_texts, batch_retrieved_texts)]
    train_summaries.extend(batch_summaries)  # Add the batch summaries to the main list

# Now, evaluate metrics for the training dataset
train_metrics = [calculate_metrics(reference, summary) for reference, summary in zip(cleaned_train_texts, train_summaries)]

# Generate summaries for the test dataset using batch processing
test_summaries = []

for i in range(0, len(cleaned_injected_test_texts), batch_size):
    batch_texts = cleaned_injected_test_texts[i:i + batch_size]
    batch_retrieved_texts = test_retrieved_texts[i:i + batch_size]

    # Generate summaries for the current batch
    batch_summaries = [generate_summary(text, retrieved_text, model, tokenizer)
                       for text, retrieved_text in zip(batch_texts, batch_retrieved_texts)]
    test_summaries.extend(batch_summaries)  # Add the batch summaries to the main list

# Now, evaluate metrics for the test dataset
test_metrics = [calculate_metrics(reference, summary) for reference, summary in zip(cleaned_test_texts, test_summaries)]


Streaming output truncated to the last 5000 lines.
  "max_position_embeddings": 514,
  "model_type": "roberta",
  "num_attention_heads": 16,
  "num_hidden_layers": 24,
  "pad_token_id": 1,
  "position_embedding_type": "absolute",
  "transformers_version": "4.42.4",
  "type_vocab_size": 1,
  "use_cache": true,
  "vocab_size": 50265
}

loading file vocab.json from cache at /root/.cache/huggingface/hub/models--roberta-large/snapshots/722cf37b1afa9454edce342e7895e588b6ff1d59/vocab.json
loading file merges.txt from cache at /root/.cache/huggingface/hub/models--roberta-large/snapshots/722cf37b1afa9454edce342e7895e588b6ff1d59/merges.txt
loading file added_tokens.json from cache at None
loading file special_tokens_map.json from cache at None
loading file tokenizer_config.json from cache at /root/.cache/huggingface/hub/models--roberta-large/snapshots/722cf37b1afa9454edce342e7895e588b6ff1d59/tokenizer_config.json
loading file tokenizer.json from cache at /root/.cache/huggingface/hub/models--robe

In [ ]:

# Display average metrics for train and test datasets
def display_average_metrics(metrics, dataset_name):
    print(f"\n{dataset_name} Dataset Evaluation:")
    avg_metrics = {metric: np.mean([m[metric] for m in metrics]) for metric in metrics[0].keys()}
    for metric, value in avg_metrics.items():
        print(f"{metric}: {value:.3f}")

display_average_metrics(train_metrics, "Train")
display_average_metrics(test_metrics, "Test")



Train Dataset Evaluation:
ROUGE-1: 0.341
ROUGE-2: 0.063
ROUGE-L: 0.201
METEOR: 0.217
BERTScore: 0.741
Precision: 0.726
Recall: 0.757
MoverScore: 0.198

Test Dataset Evaluation:
ROUGE-1: 0.299
ROUGE-2: 0.038
ROUGE-L: 0.179
METEOR: 0.177
BERTScore: 0.733
Precision: 0.713
Recall: 0.754
MoverScore: 0.217


In [ ]:
# Display original text and summary for the first 10 rows of the test data
print("\nDisplaying the first 10 rows of the test dataset:\n")
for i in range(10):
    print(f"Row {i + 1}:")
    print("Original text:", cleaned_test_texts[i])
    print("Summary:", test_summaries[i])
    print("\n")



Displaying the first 10 rows of the test dataset:

Row 1:
Original text: montague haltrecht was born in willesden north london on 27 february 1932 the third son of immigrant jewish parents his father phillip phil samuelson originally from warsaw in 1904 had come to england in 1922 aged 19 along with his family fleeing from persecution his mother kate oslovski came from a jewish family from poland who had also fled from persecution phil and kate met and married in 1923 and had five children including herbert born in 1931 norman montague and jane and a daughter who died at age 16 edith s father had kept a shoe store harold robinson s in the east end of london which he continued in early life at before moving to golders green in 1942 bill robinson was killed in action in france during the allied invasion in august 1945 while kate haltrecht died august 1946 there phil who found comfort in a friend of his wife s met and married her sometime later phil himself who as a child had been presen

**RAG with BART temp 1.5, top_k =75**

In [ ]:


# Set up the device
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')


# Load BART tokenizer and model
tokenizer = BartTokenizer.from_pretrained('facebook/bart-large')
model = BartForConditionalGeneration.from_pretrained('facebook/bart-large').to(device)

# Set the number of epochs
num_epochs = 5
train_losses = []

# Training loop with adjustable epochs
optimizer = torch.optim.Adam(model.parameters(), lr=5e-5)

for epoch in range(num_epochs):
    print(f"Epoch {epoch + 1}/{num_epochs}")

    model.train()
    epoch_train_loss = 0

    for i in range(0, len(cleaned_injected_train_texts), 4):
        batch_texts = cleaned_injected_train_texts[i:i+4]
        batch_retrieved_texts = train_retrieved_texts[i:i+4]
        input_texts = [f"Perform abstractive summarization: {text}" for text in batch_texts]

        # Check if input_texts is empty
        if not input_texts:
            raise ValueError("Input texts are empty.")

        # Print input texts for debugging
        print("Input texts:", input_texts)

        inputs = tokenizer(input_texts, return_tensors='pt', padding=True, truncation=True, max_length=512).to(device)
        label_max_length = int(0.5 * inputs['input_ids'].size(1))
        labels = tokenizer(batch_texts, return_tensors='pt', padding=True, truncation=True, max_length=label_max_length)['input_ids'].to(device)

        outputs = model(input_ids=inputs['input_ids'], attention_mask=inputs['attention_mask'], labels=labels)
        loss = outputs.loss

        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        epoch_train_loss += loss.item()

    avg_train_loss = epoch_train_loss / len(cleaned_injected_train_texts)
    train_losses.append(avg_train_loss)
    print(f"Training Loss: {avg_train_loss:.3f}")

    gc.collect()
    torch.cuda.empty_cache()

loading file vocab.json from cache at /root/.cache/huggingface/hub/models--facebook--bart-large/snapshots/cb48c1365bd826bd521f650dc2e0940aee54720c/vocab.json
loading file merges.txt from cache at /root/.cache/huggingface/hub/models--facebook--bart-large/snapshots/cb48c1365bd826bd521f650dc2e0940aee54720c/merges.txt
loading file added_tokens.json from cache at None
loading file special_tokens_map.json from cache at None
loading file tokenizer_config.json from cache at /root/.cache/huggingface/hub/models--facebook--bart-large/snapshots/cb48c1365bd826bd521f650dc2e0940aee54720c/tokenizer_config.json
loading file tokenizer.json from cache at /root/.cache/huggingface/hub/models--facebook--bart-large/snapshots/cb48c1365bd826bd521f650dc2e0940aee54720c/tokenizer.json
loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--facebook--bart-large/snapshots/cb48c1365bd826bd521f650dc2e0940aee54720c/config.json
Model config BartConfig {
  "_name_or_path": "facebook/bar

Epoch 1/5
Input texts: ['Perform abstractive summarization: christopher atkinson c 1738 23 april 1819 known as christopher atkinson savile or saville from about 1798 was an english merchant and politician the river styx forms the boundary between earth and the underworld born in yorkshire he moved to dorset and married the niece of a wealthy merchant entering that business himself he was elected at the 1780 general election as one of the two members of parliament mps for dorset west however he was expelled from the house of commons on the second sitting after being convicted of receiving a bribe and sentenced to detention in the pillory he was granted a royal warrant in 1791 and returned to parliament for the area in 1796 retaining the seat until he stood down at the 1802 general election he had changed his name to atkinson atkinson some time after 1793 hades realm is called the underworld or hades itself he then purchased extensive estates in westerleigh in hampshire which gave him co

In [ ]:


def complete_last_sentence(text):
    sentences = re.split('(?<=[.!?]) +', text)
    if len(sentences) > 1:
        if len(sentences[-1].split()) < 3:
            text = ' '.join(sentences[:-1])
        else:
            if not sentences[-1][-1] in '.!?':
                text = text + '.'
    else:
        if not text[-1] in '.!?':
            text = text + '.'
    return text

def generate_summary(text, retrieved_texts, model, tokenizer):
    text = complete_last_sentence(text)
    input_text = f"Refine the following summary using this additional context. Text: {text} Additional context: {' '.join(retrieved_texts)}"
    inputs = tokenizer.encode(input_text, return_tensors='pt', max_length=512, truncation=True).to(device)

    decoder_settings = {
        "no_repeat_ngram_size": 2,
        "max_length": int(0.5 * inputs.size(1)),
        "min_length": int(0.25 * inputs.size(1)),
        "length_penalty": 2.5,
        "temperature": 1.5,
        "top_p": 0.9,
        "top_k": 75,
        "num_beams": 5,
        "do_sample": True,
        "early_stopping": True
    }

    summary_ids = model.generate(inputs, **decoder_settings)
    final_summary = tokenizer.decode(summary_ids[0], skip_special_tokens=True)

    if not final_summary.endswith('.'):
        final_summary += '.'

    return final_summary

In [ ]:
# Initialize BERT model for evaluation
bert_tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
bert_model = BertModel.from_pretrained('bert-base-uncased')
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
bert_model.to(device)

def bert_encode(model, x, device='cpu'):
    model.eval()
    with torch.no_grad():
        x = [bert_tokenizer.encode(sent, add_special_tokens=True) for sent in x]
        x = torch.tensor(x).to(device)
        outputs = model(x)
        return outputs.last_hidden_state

loading file vocab.txt from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/vocab.txt
loading file added_tokens.json from cache at None
loading file special_tokens_map.json from cache at None
loading file tokenizer_config.json from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/tokenizer_config.json
loading file tokenizer.json from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/tokenizer.json
loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/config.json
Model config BertConfig {
  "_name_or_path": "bert-base-uncased",
  "architectures": [
    "BertForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "classifier_dropout": null,
  "gradient_checkpointing": false,
  "hidden_ac

In [ ]:




def word_mover_score(references, hypotheses, idf_dict_ref, idf_dict_hyp, stop_words=None, n_gram=1, remove_subwords=True):
    if stop_words is None:
        stop_words = []

    ref_embedding = bert_encode(bert_model.to(device), references, device)
    hyp_embedding = bert_encode(bert_model.to(device), hypotheses, device)

    ref_embedding = ref_embedding.cpu().numpy()
    hyp_embedding = hyp_embedding.cpu().numpy()

    scores = []
    for i in range(len(references)):
        ref_tokens = references[i].split()
        hyp_tokens = hypotheses[i].split()

        ref_idf = [idf_dict_ref[token] for token in ref_tokens if token not in stop_words]
        hyp_idf = [idf_dict_hyp[token] for token in hyp_tokens if token not in stop_words]

        ref_embedding_i = ref_embedding[i]
        hyp_embedding_i = hyp_embedding[i]

        max_len = max(len(ref_embedding_i), len(hyp_embedding_i))
        if len(ref_embedding_i) < max_len:
            ref_embedding_i = np.pad(ref_embedding_i, ((0, max_len - len(ref_embedding_i)), (0, 0)), mode='constant')
        if len(hyp_embedding_i) < max_len:
            hyp_embedding_i = np.pad(hyp_embedding_i, ((0, max_len - len(hyp_embedding_i)), (0, 0)), mode='constant')

        distance_matrix = np.zeros((max_len, max_len))
        for i in range(max_len):
            for j in range(max_len):
                distance_matrix[i][j] = np.linalg.norm(ref_embedding_i[i] - hyp_embedding_i[j])

        max_tokens = max(len(ref_idf), len(hyp_idf))
        ref_idf = np.pad(np.array(ref_idf), (0, max_tokens - len(ref_idf)))
        hyp_idf = np.pad(np.array(hyp_idf), (0, max_tokens - len(hyp_idf)))

        ref_idf = ref_idf / np.sum(ref_idf)
        hyp_idf = hyp_idf / np.sum(hyp_idf)

        score = emd(ref_idf, hyp_idf, distance_matrix)
        scores.append(1 / (1 + score))

    return scores

In [ ]:


# Evaluation metrics
def calculate_metrics(reference, hypothesis):
    rouge = rouge_scorer.RougeScorer(['rouge1', 'rouge2', 'rougeL'], use_stemmer=True)
    rouge_scores = rouge.score(reference, hypothesis)

    bert_precision, bert_recall, bert_f1 = bert_score([hypothesis], [reference], lang="en")

    meteor = meteor_score.meteor_score([reference.split()], hypothesis.split())

    idf_dict_ref = get_idf_dict([reference])
    idf_dict_hyp = get_idf_dict([hypothesis])
    moverscore_value = word_mover_score([reference], [hypothesis], idf_dict_ref, idf_dict_hyp)

    return {
        'ROUGE-1': rouge_scores['rouge1'].fmeasure,
        'ROUGE-2': rouge_scores['rouge2'].fmeasure,
        'ROUGE-L': rouge_scores['rougeL'].fmeasure,
        'METEOR': meteor,
        'BERTScore': bert_f1.item(),
        'Precision': bert_precision.item(),
        'Recall': bert_recall.item(),
        'MoverScore': moverscore_value[0]
    }


In [ ]:
# Move the model to the correct device
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model.to(device)

# Set batch size
batch_size = 8

# Generate summaries for the training dataset using batch processing
train_summaries = []

for i in range(0, len(cleaned_injected_train_texts), batch_size):
    batch_texts = cleaned_injected_train_texts[i:i + batch_size]
    batch_retrieved_texts = train_retrieved_texts[i:i + batch_size]

    # Generate summaries for the current batch
    batch_summaries = [generate_summary(text, retrieved_text, model, tokenizer)
                       for text, retrieved_text in zip(batch_texts, batch_retrieved_texts)]
    train_summaries.extend(batch_summaries)  # Add the batch summaries to the main list

# Now, evaluate metrics for the training dataset
train_metrics = [calculate_metrics(reference, summary) for reference, summary in zip(cleaned_train_texts, train_summaries)]

# Generate summaries for the test dataset using batch processing
test_summaries = []

for i in range(0, len(cleaned_injected_test_texts), batch_size):
    batch_texts = cleaned_injected_test_texts[i:i + batch_size]
    batch_retrieved_texts = test_retrieved_texts[i:i + batch_size]

    # Generate summaries for the current batch
    batch_summaries = [generate_summary(text, retrieved_text, model, tokenizer)
                       for text, retrieved_text in zip(batch_texts, batch_retrieved_texts)]
    test_summaries.extend(batch_summaries)  # Add the batch summaries to the main list

# Now, evaluate metrics for the test dataset
test_metrics = [calculate_metrics(reference, summary) for reference, summary in zip(cleaned_test_texts, test_summaries)]


Streaming output truncated to the last 5000 lines.
  "max_position_embeddings": 514,
  "model_type": "roberta",
  "num_attention_heads": 16,
  "num_hidden_layers": 24,
  "pad_token_id": 1,
  "position_embedding_type": "absolute",
  "transformers_version": "4.42.4",
  "type_vocab_size": 1,
  "use_cache": true,
  "vocab_size": 50265
}

loading file vocab.json from cache at /root/.cache/huggingface/hub/models--roberta-large/snapshots/722cf37b1afa9454edce342e7895e588b6ff1d59/vocab.json
loading file merges.txt from cache at /root/.cache/huggingface/hub/models--roberta-large/snapshots/722cf37b1afa9454edce342e7895e588b6ff1d59/merges.txt
loading file added_tokens.json from cache at None
loading file special_tokens_map.json from cache at None
loading file tokenizer_config.json from cache at /root/.cache/huggingface/hub/models--roberta-large/snapshots/722cf37b1afa9454edce342e7895e588b6ff1d59/tokenizer_config.json
loading file tokenizer.json from cache at /root/.cache/huggingface/hub/models--robe

In [ ]:

# Display average metrics for train and test datasets
def display_average_metrics(metrics, dataset_name):
    print(f"\n{dataset_name} Dataset Evaluation:")
    avg_metrics = {metric: np.mean([m[metric] for m in metrics]) for metric in metrics[0].keys()}
    for metric, value in avg_metrics.items():
        print(f"{metric}: {value:.3f}")

display_average_metrics(train_metrics, "Train")
display_average_metrics(test_metrics, "Test")



Train Dataset Evaluation:
ROUGE-1: 0.684
ROUGE-2: 0.604
ROUGE-L: 0.621
METEOR: 0.556
BERTScore: 0.910
Precision: 0.913
Recall: 0.906
MoverScore: 0.278

Test Dataset Evaluation:
ROUGE-1: 0.674
ROUGE-2: 0.613
ROUGE-L: 0.641
METEOR: 0.541
BERTScore: 0.914
Precision: 0.925
Recall: 0.904
MoverScore: 0.265


In [ ]:
# Display original text and summary for the first 10 rows of the test data
print("\nDisplaying the first 10 rows of the test dataset:\n")
for i in range(10):
    print(f"Row {i + 1}:")
    print("Original text:", cleaned_test_texts[i])
    print("Summary:", test_summaries[i])
    print("\n")



Displaying the first 10 rows of the test dataset:

Row 1:
Original text: montague haltrecht was born in willesden north london on 27 february 1932 the third son of immigrant jewish parents his father phillip phil samuelson originally from warsaw in 1904 had come to england in 1922 aged 19 along with his family fleeing from persecution his mother kate oslovski came from a jewish family from poland who had also fled from persecution phil and kate met and married in 1923 and had five children including herbert born in 1931 norman montague and jane and a daughter who died at age 16 edith s father had kept a shoe store harold robinson s in the east end of london which he continued in early life at before moving to golders green in 1942 bill robinson was killed in action in france during the allied invasion in august 1945 while kate haltrecht died august 1946 there phil who found comfort in a friend of his wife s met and married her sometime later phil himself who as a child had been presen

**BART with RAG 2-step summarisation**

In [ ]:


# Set up the device
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')


# Load BART tokenizer and model
tokenizer = BartTokenizer.from_pretrained('facebook/bart-large')
model = BartForConditionalGeneration.from_pretrained('facebook/bart-large').to(device)

# Set the number of epochs
num_epochs = 5
train_losses = []

# Training loop with adjustable epochs
optimizer = torch.optim.Adam(model.parameters(), lr=5e-5)

for epoch in range(num_epochs):
    print(f"Epoch {epoch + 1}/{num_epochs}")

    model.train()
    epoch_train_loss = 0

    for i in range(0, len(cleaned_injected_train_texts), 4):
        batch_texts = cleaned_injected_train_texts[i:i+4]
        batch_retrieved_texts = train_retrieved_texts[i:i+4]
        input_texts = [f"Perform abstractive summarization: {text}" for text in batch_texts]

        # Check if input_texts is empty
        if not input_texts:
            raise ValueError("Input texts are empty.")

        # Print input texts for debugging
        print("Input texts:", input_texts)

        inputs = tokenizer(input_texts, return_tensors='pt', padding=True, truncation=True, max_length=512).to(device)
        label_max_length = int(0.5 * inputs['input_ids'].size(1))
        labels = tokenizer(batch_texts, return_tensors='pt', padding=True, truncation=True, max_length=label_max_length)['input_ids'].to(device)

        outputs = model(input_ids=inputs['input_ids'], attention_mask=inputs['attention_mask'], labels=labels)
        loss = outputs.loss

        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        epoch_train_loss += loss.item()

    avg_train_loss = epoch_train_loss / len(cleaned_injected_train_texts)
    train_losses.append(avg_train_loss)
    print(f"Training Loss: {avg_train_loss:.3f}")

    gc.collect()
    torch.cuda.empty_cache()

loading file vocab.json from cache at /root/.cache/huggingface/hub/models--facebook--bart-large/snapshots/cb48c1365bd826bd521f650dc2e0940aee54720c/vocab.json
loading file merges.txt from cache at /root/.cache/huggingface/hub/models--facebook--bart-large/snapshots/cb48c1365bd826bd521f650dc2e0940aee54720c/merges.txt
loading file added_tokens.json from cache at None
loading file special_tokens_map.json from cache at None
loading file tokenizer_config.json from cache at /root/.cache/huggingface/hub/models--facebook--bart-large/snapshots/cb48c1365bd826bd521f650dc2e0940aee54720c/tokenizer_config.json
loading file tokenizer.json from cache at /root/.cache/huggingface/hub/models--facebook--bart-large/snapshots/cb48c1365bd826bd521f650dc2e0940aee54720c/tokenizer.json
loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--facebook--bart-large/snapshots/cb48c1365bd826bd521f650dc2e0940aee54720c/config.json
Model config BartConfig {
  "_name_or_path": "facebook/bar

Epoch 1/5
Input texts: ['Perform abstractive summarization: christopher atkinson c 1738 23 april 1819 known as christopher atkinson savile or saville from about 1798 was an english merchant and politician the river styx forms the boundary between earth and the underworld born in yorkshire he moved to dorset and married the niece of a wealthy merchant entering that business himself he was elected at the 1780 general election as one of the two members of parliament mps for dorset west however he was expelled from the house of commons on the second sitting after being convicted of receiving a bribe and sentenced to detention in the pillory he was granted a royal warrant in 1791 and returned to parliament for the area in 1796 retaining the seat until he stood down at the 1802 general election he had changed his name to atkinson atkinson some time after 1793 hades realm is called the underworld or hades itself he then purchased extensive estates in westerleigh in hampshire which gave him co

In [ ]:
import re
import torch

def complete_last_sentence(text):
    sentences = re.split('(?<=[.!?]) +', text)
    if len(sentences) > 1:
        if len(sentences[-1].split()) < 3:
            text = ' '.join(sentences[:-1])
        else:
            if not sentences[-1][-1] in '.!?':
                text = text + '.'
    else:
        if not text[-1] in '.!?':
            text = text + '.'
    return text

def generate_summary(text, retrieved_texts, model, tokenizer, device):
    text = complete_last_sentence(text)
    input_text = f"Refine the following summary using this additional context. Text: {text} Additional context: {' '.join(retrieved_texts)}"
    inputs = tokenizer.encode(input_text, return_tensors='pt', max_length=512, truncation=True).to(device)

    decoder_settings = {
        "no_repeat_ngram_size": 2,
        "max_length": int(0.5 * inputs.size(1)),
        "min_length": int(0.25 * inputs.size(1)),
        "length_penalty": 2.5,
        "temperature": 0.7,
        "top_p": 0.9,
        "top_k": 50,
        "num_beams": 5,
        "do_sample": False,
        "early_stopping": True
    }

    summary_ids = model.generate(inputs, **decoder_settings)
    final_summary = tokenizer.decode(summary_ids[0], skip_special_tokens=True)

    if not final_summary.endswith('.'):
        final_summary += '.'

    return final_summary


In [ ]:
# Initialize BERT model for evaluation
bert_tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
bert_model = BertModel.from_pretrained('bert-base-uncased')
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
bert_model.to(device)

def bert_encode(model, x, device='cpu'):
    model.eval()
    with torch.no_grad():
        x = [bert_tokenizer.encode(sent, add_special_tokens=True) for sent in x]
        x = torch.tensor(x).to(device)
        outputs = model(x)
        return outputs.last_hidden_state

loading file vocab.txt from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/vocab.txt
loading file added_tokens.json from cache at None
loading file special_tokens_map.json from cache at None
loading file tokenizer_config.json from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/tokenizer_config.json
loading file tokenizer.json from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/tokenizer.json
loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/config.json
Model config BertConfig {
  "_name_or_path": "bert-base-uncased",
  "architectures": [
    "BertForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "classifier_dropout": null,
  "gradient_checkpointing": false,
  "hidden_ac

In [ ]:




def word_mover_score(references, hypotheses, idf_dict_ref, idf_dict_hyp, stop_words=None, n_gram=1, remove_subwords=True):
    if stop_words is None:
        stop_words = []

    ref_embedding = bert_encode(bert_model.to(device), references, device)
    hyp_embedding = bert_encode(bert_model.to(device), hypotheses, device)

    ref_embedding = ref_embedding.cpu().numpy()
    hyp_embedding = hyp_embedding.cpu().numpy()

    scores = []
    for i in range(len(references)):
        ref_tokens = references[i].split()
        hyp_tokens = hypotheses[i].split()

        ref_idf = [idf_dict_ref[token] for token in ref_tokens if token not in stop_words]
        hyp_idf = [idf_dict_hyp[token] for token in hyp_tokens if token not in stop_words]

        ref_embedding_i = ref_embedding[i]
        hyp_embedding_i = hyp_embedding[i]

        max_len = max(len(ref_embedding_i), len(hyp_embedding_i))
        if len(ref_embedding_i) < max_len:
            ref_embedding_i = np.pad(ref_embedding_i, ((0, max_len - len(ref_embedding_i)), (0, 0)), mode='constant')
        if len(hyp_embedding_i) < max_len:
            hyp_embedding_i = np.pad(hyp_embedding_i, ((0, max_len - len(hyp_embedding_i)), (0, 0)), mode='constant')

        distance_matrix = np.zeros((max_len, max_len))
        for i in range(max_len):
            for j in range(max_len):
                distance_matrix[i][j] = np.linalg.norm(ref_embedding_i[i] - hyp_embedding_i[j])

        max_tokens = max(len(ref_idf), len(hyp_idf))
        ref_idf = np.pad(np.array(ref_idf), (0, max_tokens - len(ref_idf)))
        hyp_idf = np.pad(np.array(hyp_idf), (0, max_tokens - len(hyp_idf)))

        ref_idf = ref_idf / np.sum(ref_idf)
        hyp_idf = hyp_idf / np.sum(hyp_idf)

        score = emd(ref_idf, hyp_idf, distance_matrix)
        scores.append(1 / (1 + score))

    return scores

In [ ]:


# Evaluation metrics
def calculate_metrics(reference, hypothesis):
    rouge = rouge_scorer.RougeScorer(['rouge1', 'rouge2', 'rougeL'], use_stemmer=True)
    rouge_scores = rouge.score(reference, hypothesis)

    bert_precision, bert_recall, bert_f1 = bert_score([hypothesis], [reference], lang="en")

    meteor = meteor_score.meteor_score([reference.split()], hypothesis.split())

    idf_dict_ref = get_idf_dict([reference])
    idf_dict_hyp = get_idf_dict([hypothesis])
    moverscore_value = word_mover_score([reference], [hypothesis], idf_dict_ref, idf_dict_hyp)

    return {
        'ROUGE-1': rouge_scores['rouge1'].fmeasure,
        'ROUGE-2': rouge_scores['rouge2'].fmeasure,
        'ROUGE-L': rouge_scores['rougeL'].fmeasure,
        'METEOR': meteor,
        'BERTScore': bert_f1.item(),
        'Precision': bert_precision.item(),
        'Recall': bert_recall.item(),
        'MoverScore': moverscore_value[0]
    }


In [ ]:
import torch

# Move the model to the correct device
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model.to(device)

# Set batch size
batch_size = 8

# Generate summaries for the training dataset using batch processing
train_intermediate_summaries = []
train_final_summaries = []

for i in range(0, len(cleaned_injected_train_texts), batch_size):
    batch_texts = cleaned_injected_train_texts[i:i + batch_size]
    batch_retrieved_texts = train_retrieved_texts[i:i + batch_size]

    # Step 1: Generate intermediate summaries for the current batch
    intermediate_summaries = [generate_summary(text, retrieved_text, model, tokenizer, device)
                               for text, retrieved_text in zip(batch_texts, batch_retrieved_texts)]
    train_intermediate_summaries.extend(intermediate_summaries)  # Store intermediate summaries

    # Step 2: Generate final summaries from the intermediate summaries
    final_summaries = [generate_summary(intermediate, [], model, tokenizer, device)
                       for intermediate in intermediate_summaries]  # Assuming no additional context for final summaries
    train_final_summaries.extend(final_summaries)  # Store final summaries

# Now, evaluate metrics for the training dataset
train_metrics = [calculate_metrics(reference, summary) for reference, summary in zip(cleaned_train_texts, train_final_summaries)]

# Generate summaries for the test dataset using batch processing
test_intermediate_summaries = []
test_final_summaries = []

for i in range(0, len(cleaned_injected_test_texts), batch_size):
    batch_texts = cleaned_injected_test_texts[i:i + batch_size]
    batch_retrieved_texts = test_retrieved_texts[i:i + batch_size]

    # Step 1: Generate intermediate summaries for the current batch
    intermediate_summaries = [generate_summary(text, retrieved_text, model, tokenizer, device)
                               for text, retrieved_text in zip(batch_texts, batch_retrieved_texts)]
    test_intermediate_summaries.extend(intermediate_summaries)  # Store intermediate summaries

    # Step 2: Generate final summaries from the intermediate summaries
    final_summaries = [generate_summary(intermediate, [], model, tokenizer, device)
                       for intermediate in intermediate_summaries]  # Assuming no additional context for final summaries
    test_final_summaries.extend(final_summaries)  # Store final summaries

# Now, evaluate metrics for the test dataset
test_metrics = [calculate_metrics(reference, summary) for reference, summary in zip(cleaned_test_texts, test_final_summaries)]


Streaming output truncated to the last 5000 lines.
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 0,
  "classifier_dropout": null,
  "eos_token_id": 2,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 1024,
  "initializer_range": 0.02,
  "intermediate_size": 4096,
  "layer_norm_eps": 1e-05,
  "max_position_embeddings": 514,
  "model_type": "roberta",
  "num_attention_heads": 16,
  "num_hidden_layers": 24,
  "pad_token_id": 1,
  "position_embedding_type": "absolute",
  "transformers_version": "4.42.4",
  "type_vocab_size": 1,
  "use_cache": true,
  "vocab_size": 50265
}

loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--roberta-large/snapshots/722cf37b1afa9454edce342e7895e588b6ff1d59/config.json
Model config RobertaConfig {
  "_name_or_path": "roberta-large",
  "architectures": [
    "RobertaForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 0,
  "classifier_dropout": null,
  "eos_token_id": 

In [ ]:

# Display average metrics for train and test datasets
def display_average_metrics(metrics, dataset_name):
    print(f"\n{dataset_name} Dataset Evaluation:")
    avg_metrics = {metric: np.mean([m[metric] for m in metrics]) for metric in metrics[0].keys()}
    for metric, value in avg_metrics.items():
        print(f"{metric}: {value:.3f}")

display_average_metrics(train_metrics, "Train")
display_average_metrics(test_metrics, "Test")



Train Dataset Evaluation:
ROUGE-1: 0.418
ROUGE-2: 0.373
ROUGE-L: 0.390
METEOR: 0.249
BERTScore: 0.878
Precision: 0.915
Recall: 0.845
MoverScore: 0.102

Test Dataset Evaluation:
ROUGE-1: 0.397
ROUGE-2: 0.369
ROUGE-L: 0.378
METEOR: 0.232
BERTScore: 0.878
Precision: 0.919
Recall: 0.840
MoverScore: 0.092


In [ ]:
# Displaying the first 10 rows of the test dataset
for i in range(10):
    print(f"Row {i + 1}:")
    print("Original text:", cleaned_test_texts[i])
    print("Summary:", test_final_summaries[i])  # Use test_final_summaries instead of test_summaries
    print("\n")


Row 1:
Original text: montague haltrecht was born in willesden north london on 27 february 1932 the third son of immigrant jewish parents his father phillip phil samuelson originally from warsaw in 1904 had come to england in 1922 aged 19 along with his family fleeing from persecution his mother kate oslovski came from a jewish family from poland who had also fled from persecution phil and kate met and married in 1923 and had five children including herbert born in 1931 norman montague and jane and a daughter who died at age 16 edith s father had kept a shoe store harold robinson s in the east end of london which he continued in early life at before moving to golders green in 1942 bill robinson was killed in action in france during the allied invasion in august 1945 while kate haltrecht died august 1946 there phil who found comfort in a friend of his wife s met and married her sometime later phil himself who as a child had been presented with complete translations of the works of both 

**RAG Implementation with T5**

**Temp 0.7**

In [ ]:


# Set up the device
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')


# Load T5-large tokenizer and model
tokenizer = T5Tokenizer.from_pretrained('t5-large')
model = T5ForConditionalGeneration.from_pretrained('t5-large').to(device)

# Set the number of epochs
num_epochs = 5
train_losses = []

# Training loop with adjustable epochs
optimizer = torch.optim.Adam(model.parameters(), lr=5e-5)

for epoch in range(num_epochs):
    print(f"Epoch {epoch + 1}/{num_epochs}")

    model.train()
    epoch_train_loss = 0

    for i in range(0, len(cleaned_injected_train_texts), 4):  # Batch size of 4
        batch_texts = cleaned_injected_train_texts[i:i+4]
        batch_retrieved_texts = train_retrieved_texts[i:i+4]
        input_texts = [f"Perform abstractive summarization: {text}" for text in batch_texts]

        # Check if input_texts is empty
        if not input_texts:
            raise ValueError("Input texts are empty.")

        # Print input texts for debugging
        print("Input texts:", input_texts)

        inputs = tokenizer(input_texts, return_tensors='pt', padding=True, truncation=True, max_length=512).to(device)
        label_max_length = int(0.5 * inputs['input_ids'].size(1))
        labels = tokenizer(batch_texts, return_tensors='pt', padding=True, truncation=True, max_length=label_max_length)['input_ids'].to(device)

        outputs = model(input_ids=inputs['input_ids'], attention_mask=inputs['attention_mask'], labels=labels)
        loss = outputs.loss

        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        epoch_train_loss += loss.item()

    avg_train_loss = epoch_train_loss / len(cleaned_injected_train_texts)
    train_losses.append(avg_train_loss)
    print(f"Training Loss: {avg_train_loss:.3f}")

    gc.collect()
    torch.cuda.empty_cache()

spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.39M [00:00<?, ?B/s]

loading file spiece.model from cache at /root/.cache/huggingface/hub/models--t5-large/snapshots/150ebc2c4b72291e770f58e6057481c8d2ed331a/spiece.model
loading file added_tokens.json from cache at None
loading file special_tokens_map.json from cache at None
loading file tokenizer_config.json from cache at None
loading file tokenizer.json from cache at /root/.cache/huggingface/hub/models--t5-large/snapshots/150ebc2c4b72291e770f58e6057481c8d2ed331a/tokenizer.json


config.json:   0%|          | 0.00/1.21k [00:00<?, ?B/s]

loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--t5-large/snapshots/150ebc2c4b72291e770f58e6057481c8d2ed331a/config.json
Model config T5Config {
  "_name_or_path": "t5-large",
  "architectures": [
    "T5ForConditionalGeneration"
  ],
  "classifier_dropout": 0.0,
  "d_ff": 4096,
  "d_kv": 64,
  "d_model": 1024,
  "decoder_start_token_id": 0,
  "dense_act_fn": "relu",
  "dropout_rate": 0.1,
  "eos_token_id": 1,
  "feed_forward_proj": "relu",
  "initializer_factor": 1.0,
  "is_encoder_decoder": true,
  "is_gated_act": false,
  "layer_norm_epsilon": 1e-06,
  "model_type": "t5",
  "n_positions": 512,
  "num_decoder_layers": 24,
  "num_heads": 16,
  "num_layers": 24,
  "output_past": true,
  "pad_token_id": 0,
  "relative_attention_max_distance": 128,
  "relative_attention_num_buckets": 32,
  "task_specific_params": {
    "summarization": {
      "early_stopping": true,
      "length_penalty": 2.0,
      "max_length": 200,
      "min_length": 30,
   

model.safetensors:   0%|          | 0.00/2.95G [00:00<?, ?B/s]

loading weights file model.safetensors from cache at /root/.cache/huggingface/hub/models--t5-large/snapshots/150ebc2c4b72291e770f58e6057481c8d2ed331a/model.safetensors
Generate config GenerationConfig {
  "decoder_start_token_id": 0,
  "eos_token_id": 1,
  "pad_token_id": 0
}

All model checkpoint weights were used when initializing T5ForConditionalGeneration.

All the weights of T5ForConditionalGeneration were initialized from the model checkpoint at t5-large.
If your task is similar to the task the model of the checkpoint was trained on, you can already use T5ForConditionalGeneration for predictions without further training.


generation_config.json:   0%|          | 0.00/147 [00:00<?, ?B/s]

loading configuration file generation_config.json from cache at /root/.cache/huggingface/hub/models--t5-large/snapshots/150ebc2c4b72291e770f58e6057481c8d2ed331a/generation_config.json
Generate config GenerationConfig {
  "decoder_start_token_id": 0,
  "eos_token_id": 1,
  "pad_token_id": 0
}



Epoch 1/5
Input texts: ['Perform abstractive summarization: christopher atkinson c 1738 23 april 1819 known as christopher atkinson savile or saville from about 1798 was an english merchant and politician the river styx forms the boundary between earth and the underworld born in yorkshire he moved to dorset and married the niece of a wealthy merchant entering that business himself he was elected at the 1780 general election as one of the two members of parliament mps for dorset west however he was expelled from the house of commons on the second sitting after being convicted of receiving a bribe and sentenced to detention in the pillory he was granted a royal warrant in 1791 and returned to parliament for the area in 1796 retaining the seat until he stood down at the 1802 general election he had changed his name to atkinson atkinson some time after 1793 hades realm is called the underworld or hades itself he then purchased extensive estates in westerleigh in hampshire which gave him co

In [ ]:


def complete_last_sentence(text):
    sentences = re.split('(?<=[.!?]) +', text)
    if len(sentences) > 1:
        if len(sentences[-1].split()) < 3:
            text = ' '.join(sentences[:-1])
        else:
            if not sentences[-1][-1] in '.!?':
                text = text + '.'
    else:
        if not text[-1] in '.!?':
            text = text + '.'
    return text

def generate_summary(text, retrieved_texts, model, tokenizer):
    text = complete_last_sentence(text)
    input_text = f"Refine the following summary using this additional context. Text: {text} Additional context: {' '.join(retrieved_texts)}"
    inputs = tokenizer.encode(input_text, return_tensors='pt', max_length=512, truncation=True).to(device)

    decoder_settings = {
        "no_repeat_ngram_size": 2,
        "max_length": int(0.5 * inputs.size(1)),
        "min_length": int(0.25 * inputs.size(1)),
        "length_penalty": 2.5,
        "temperature": 0.7,
        "top_p": 0.9,
        "top_k": 50,
        "num_beams": 5,
        "do_sample": True,
        "early_stopping": True
    }

    summary_ids = model.generate(inputs, **decoder_settings)
    final_summary = tokenizer.decode(summary_ids[0], skip_special_tokens=True)

    if not final_summary.endswith('.'):
        final_summary += '.'

    return final_summary

In [ ]:
# Initialize BERT model for evaluation
bert_tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
bert_model = BertModel.from_pretrained('bert-base-uncased')
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
bert_model.to(device)

def bert_encode(model, x, device='cpu'):
    model.eval()
    with torch.no_grad():
        x = [bert_tokenizer.encode(sent, add_special_tokens=True) for sent in x]
        x = torch.tensor(x).to(device)
        outputs = model(x)
        return outputs.last_hidden_state

loading file vocab.txt from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/vocab.txt
loading file added_tokens.json from cache at None
loading file special_tokens_map.json from cache at None
loading file tokenizer_config.json from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/tokenizer_config.json
loading file tokenizer.json from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/tokenizer.json
loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/config.json
Model config BertConfig {
  "_name_or_path": "bert-base-uncased",
  "architectures": [
    "BertForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "classifier_dropout": null,
  "gradient_checkpointing": false,
  "hidden_ac

In [ ]:




def word_mover_score(references, hypotheses, idf_dict_ref, idf_dict_hyp, stop_words=None, n_gram=1, remove_subwords=True):
    if stop_words is None:
        stop_words = []

    ref_embedding = bert_encode(bert_model.to(device), references, device)
    hyp_embedding = bert_encode(bert_model.to(device), hypotheses, device)

    ref_embedding = ref_embedding.cpu().numpy()
    hyp_embedding = hyp_embedding.cpu().numpy()

    scores = []
    for i in range(len(references)):
        ref_tokens = references[i].split()
        hyp_tokens = hypotheses[i].split()

        ref_idf = [idf_dict_ref[token] for token in ref_tokens if token not in stop_words]
        hyp_idf = [idf_dict_hyp[token] for token in hyp_tokens if token not in stop_words]

        ref_embedding_i = ref_embedding[i]
        hyp_embedding_i = hyp_embedding[i]

        max_len = max(len(ref_embedding_i), len(hyp_embedding_i))
        if len(ref_embedding_i) < max_len:
            ref_embedding_i = np.pad(ref_embedding_i, ((0, max_len - len(ref_embedding_i)), (0, 0)), mode='constant')
        if len(hyp_embedding_i) < max_len:
            hyp_embedding_i = np.pad(hyp_embedding_i, ((0, max_len - len(hyp_embedding_i)), (0, 0)), mode='constant')

        distance_matrix = np.zeros((max_len, max_len))
        for i in range(max_len):
            for j in range(max_len):
                distance_matrix[i][j] = np.linalg.norm(ref_embedding_i[i] - hyp_embedding_i[j])

        max_tokens = max(len(ref_idf), len(hyp_idf))
        ref_idf = np.pad(np.array(ref_idf), (0, max_tokens - len(ref_idf)))
        hyp_idf = np.pad(np.array(hyp_idf), (0, max_tokens - len(hyp_idf)))

        ref_idf = ref_idf / np.sum(ref_idf)
        hyp_idf = hyp_idf / np.sum(hyp_idf)

        score = emd(ref_idf, hyp_idf, distance_matrix)
        scores.append(1 / (1 + score))

    return scores

In [ ]:


# Evaluation metrics
def calculate_metrics(reference, hypothesis):
    rouge = rouge_scorer.RougeScorer(['rouge1', 'rouge2', 'rougeL'], use_stemmer=True)
    rouge_scores = rouge.score(reference, hypothesis)

    bert_precision, bert_recall, bert_f1 = bert_score([hypothesis], [reference], lang="en")

    meteor = meteor_score.meteor_score([reference.split()], hypothesis.split())

    idf_dict_ref = get_idf_dict([reference])
    idf_dict_hyp = get_idf_dict([hypothesis])
    moverscore_value = word_mover_score([reference], [hypothesis], idf_dict_ref, idf_dict_hyp)

    return {
        'ROUGE-1': rouge_scores['rouge1'].fmeasure,
        'ROUGE-2': rouge_scores['rouge2'].fmeasure,
        'ROUGE-L': rouge_scores['rougeL'].fmeasure,
        'METEOR': meteor,
        'BERTScore': bert_f1.item(),
        'Precision': bert_precision.item(),
        'Recall': bert_recall.item(),
        'MoverScore': moverscore_value[0]
    }


In [ ]:
# Move the model to the correct device
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model.to(device)

# Set batch size
batch_size = 8  # Adjust based on your GPU memory

# Generate summaries for the training dataset using batch processing
train_summaries = []

for i in range(0, len(cleaned_injected_train_texts), batch_size):
    batch_texts = cleaned_injected_train_texts[i:i + batch_size]
    batch_retrieved_texts = train_retrieved_texts[i:i + batch_size]

    # Generate summaries for the current batch
    batch_summaries = [generate_summary(text, retrieved_text, model, tokenizer)
                       for text, retrieved_text in zip(batch_texts, batch_retrieved_texts)]
    train_summaries.extend(batch_summaries)  # Add the batch summaries to the main list

# Now, evaluate metrics for the training dataset
train_metrics = [calculate_metrics(reference, summary) for reference, summary in zip(cleaned_train_texts, train_summaries)]

# Generate summaries for the test dataset using batch processing
test_summaries = []

for i in range(0, len(cleaned_injected_test_texts), batch_size):
    batch_texts = cleaned_injected_test_texts[i:i + batch_size]
    batch_retrieved_texts = test_retrieved_texts[i:i + batch_size]

    # Generate summaries for the current batch
    batch_summaries = [generate_summary(text, retrieved_text, model, tokenizer)
                       for text, retrieved_text in zip(batch_texts, batch_retrieved_texts)]
    test_summaries.extend(batch_summaries)  # Add the batch summaries to the main list

# Now, evaluate metrics for the test dataset
test_metrics = [calculate_metrics(reference, summary) for reference, summary in zip(cleaned_test_texts, test_summaries)]


Streaming output truncated to the last 5000 lines.
}

loading weights file model.safetensors from cache at /root/.cache/huggingface/hub/models--roberta-large/snapshots/722cf37b1afa9454edce342e7895e588b6ff1d59/model.safetensors
Some weights of the model checkpoint at roberta-large were not used when initializing RobertaModel: ['lm_head.bias', 'lm_head.dense.bias', 'lm_head.dense.weight', 'lm_head.layer_norm.bias', 'lm_head.layer_norm.weight']
- This IS expected if you are initializing RobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaModel were not initialized from the model checkpoint at roberta-large an

In [ ]:

# Display average metrics for train and test datasets
def display_average_metrics(metrics, dataset_name):
    print(f"\n{dataset_name} Dataset Evaluation:")
    avg_metrics = {metric: np.mean([m[metric] for m in metrics]) for metric in metrics[0].keys()}
    for metric, value in avg_metrics.items():
        print(f"{metric}: {value:.3f}")

display_average_metrics(train_metrics, "Train")
display_average_metrics(test_metrics, "Test")



Train Dataset Evaluation:
ROUGE-1: 0.681
ROUGE-2: 0.595
ROUGE-L: 0.643
METEOR: 0.530
BERTScore: 0.913
Precision: 0.922
Recall: 0.906
MoverScore: 0.231

Test Dataset Evaluation:
ROUGE-1: 0.703
ROUGE-2: 0.646
ROUGE-L: 0.690
METEOR: 0.554
BERTScore: 0.921
Precision: 0.938
Recall: 0.905
MoverScore: 0.267


In [ ]:
# Display original text and summary for the first 10 rows of the test data
print("\nDisplaying the first 10 rows of the test dataset:\n")
for i in range(10):
    print(f"Row {i + 1}:")
    print("Original text:", cleaned_test_texts[i])
    print("Summary:", test_summaries[i])
    print("\n")



Displaying the first 10 rows of the test dataset:

Row 1:
Original text: montague haltrecht was born in willesden north london on 27 february 1932 the third son of immigrant jewish parents his father phillip phil samuelson originally from warsaw in 1904 had come to england in 1922 aged 19 along with his family fleeing from persecution his mother kate oslovski came from a jewish family from poland who had also fled from persecution phil and kate met and married in 1923 and had five children including herbert born in 1931 norman montague and jane and a daughter who died at age 16 edith s father had kept a shoe store harold robinson s in the east end of london which he continued in early life at before moving to golders green in 1942 bill robinson was killed in action in france during the allied invasion in august 1945 while kate haltrecht died august 1946 there phil who found comfort in a friend of his wife s met and married her sometime later phil himself who as a child had been presen

**RAG with T5 at temp 1.5, top_k 75**

In [ ]:


# Set up the device
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')


# Load T5-large tokenizer and model
tokenizer = T5Tokenizer.from_pretrained('t5-large')
model = T5ForConditionalGeneration.from_pretrained('t5-large').to(device)

# Set the number of epochs
num_epochs = 5
train_losses = []

# Training loop with adjustable epochs
optimizer = torch.optim.Adam(model.parameters(), lr=5e-5)

for epoch in range(num_epochs):
    print(f"Epoch {epoch + 1}/{num_epochs}")

    model.train()
    epoch_train_loss = 0

    for i in range(0, len(cleaned_injected_train_texts), 4):
        batch_texts = cleaned_injected_train_texts[i:i+4]
        batch_retrieved_texts = train_retrieved_texts[i:i+4]
        input_texts = [f"Perform abstractive summarization: {text}" for text in batch_texts]

        # Check if input_texts is empty
        if not input_texts:
            raise ValueError("Input texts are empty.")

        # Print input texts for debugging
        print("Input texts:", input_texts)

        inputs = tokenizer(input_texts, return_tensors='pt', padding=True, truncation=True, max_length=512).to(device)
        label_max_length = int(0.5 * inputs['input_ids'].size(1))
        labels = tokenizer(batch_texts, return_tensors='pt', padding=True, truncation=True, max_length=label_max_length)['input_ids'].to(device)

        outputs = model(input_ids=inputs['input_ids'], attention_mask=inputs['attention_mask'], labels=labels)
        loss = outputs.loss

        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        epoch_train_loss += loss.item()

    avg_train_loss = epoch_train_loss / len(cleaned_injected_train_texts)
    train_losses.append(avg_train_loss)
    print(f"Training Loss: {avg_train_loss:.3f}")

    gc.collect()
    torch.cuda.empty_cache()

loading file spiece.model from cache at /root/.cache/huggingface/hub/models--t5-large/snapshots/150ebc2c4b72291e770f58e6057481c8d2ed331a/spiece.model
loading file added_tokens.json from cache at None
loading file special_tokens_map.json from cache at None
loading file tokenizer_config.json from cache at None
loading file tokenizer.json from cache at /root/.cache/huggingface/hub/models--t5-large/snapshots/150ebc2c4b72291e770f58e6057481c8d2ed331a/tokenizer.json
loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--t5-large/snapshots/150ebc2c4b72291e770f58e6057481c8d2ed331a/config.json
Model config T5Config {
  "_name_or_path": "t5-large",
  "architectures": [
    "T5ForConditionalGeneration"
  ],
  "classifier_dropout": 0.0,
  "d_ff": 4096,
  "d_kv": 64,
  "d_model": 1024,
  "decoder_start_token_id": 0,
  "dense_act_fn": "relu",
  "dropout_rate": 0.1,
  "eos_token_id": 1,
  "feed_forward_proj": "relu",
  "initializer_factor": 1.0,
  "is_encoder_decoder

Epoch 1/5
Input texts: ['Perform abstractive summarization: christopher atkinson c 1738 23 april 1819 known as christopher atkinson savile or saville from about 1798 was an english merchant and politician the river styx forms the boundary between earth and the underworld born in yorkshire he moved to dorset and married the niece of a wealthy merchant entering that business himself he was elected at the 1780 general election as one of the two members of parliament mps for dorset west however he was expelled from the house of commons on the second sitting after being convicted of receiving a bribe and sentenced to detention in the pillory he was granted a royal warrant in 1791 and returned to parliament for the area in 1796 retaining the seat until he stood down at the 1802 general election he had changed his name to atkinson atkinson some time after 1793 hades realm is called the underworld or hades itself he then purchased extensive estates in westerleigh in hampshire which gave him co

In [ ]:


def complete_last_sentence(text):
    sentences = re.split('(?<=[.!?]) +', text)
    if len(sentences) > 1:
        if len(sentences[-1].split()) < 3:
            text = ' '.join(sentences[:-1])
        else:
            if not sentences[-1][-1] in '.!?':
                text = text + '.'
    else:
        if not text[-1] in '.!?':
            text = text + '.'
    return text

def generate_summary(text, retrieved_texts, model, tokenizer):
    text = complete_last_sentence(text)
    input_text = f"Refine the following summary using this additional context. Text: {text} Additional context: {' '.join(retrieved_texts)}"
    inputs = tokenizer.encode(input_text, return_tensors='pt', max_length=512, truncation=True).to(device)

    decoder_settings = {
        "no_repeat_ngram_size": 2,
        "max_length": int(0.5 * inputs.size(1)),
        "min_length": int(0.25 * inputs.size(1)),
        "length_penalty": 2.5,
        "temperature": 1.5,
        "top_p": 0.9,
        "top_k": 75,
        "num_beams": 5,
        "do_sample": True,
        "early_stopping": True
    }

    summary_ids = model.generate(inputs, **decoder_settings)
    final_summary = tokenizer.decode(summary_ids[0], skip_special_tokens=True)

    if not final_summary.endswith('.'):
        final_summary += '.'

    return final_summary

In [ ]:
# Initialize BERT model for evaluation
bert_tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
bert_model = BertModel.from_pretrained('bert-base-uncased')
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
bert_model.to(device)

def bert_encode(model, x, device='cpu'):
    model.eval()
    with torch.no_grad():
        x = [bert_tokenizer.encode(sent, add_special_tokens=True) for sent in x]
        x = torch.tensor(x).to(device)
        outputs = model(x)
        return outputs.last_hidden_state

loading file vocab.txt from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/vocab.txt
loading file added_tokens.json from cache at None
loading file special_tokens_map.json from cache at None
loading file tokenizer_config.json from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/tokenizer_config.json
loading file tokenizer.json from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/tokenizer.json
loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/config.json
Model config BertConfig {
  "_name_or_path": "bert-base-uncased",
  "architectures": [
    "BertForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "classifier_dropout": null,
  "gradient_checkpointing": false,
  "hidden_ac

In [ ]:




def word_mover_score(references, hypotheses, idf_dict_ref, idf_dict_hyp, stop_words=None, n_gram=1, remove_subwords=True):
    if stop_words is None:
        stop_words = []

    ref_embedding = bert_encode(bert_model.to(device), references, device)
    hyp_embedding = bert_encode(bert_model.to(device), hypotheses, device)

    ref_embedding = ref_embedding.cpu().numpy()
    hyp_embedding = hyp_embedding.cpu().numpy()

    scores = []
    for i in range(len(references)):
        ref_tokens = references[i].split()
        hyp_tokens = hypotheses[i].split()

        ref_idf = [idf_dict_ref[token] for token in ref_tokens if token not in stop_words]
        hyp_idf = [idf_dict_hyp[token] for token in hyp_tokens if token not in stop_words]

        ref_embedding_i = ref_embedding[i]
        hyp_embedding_i = hyp_embedding[i]

        max_len = max(len(ref_embedding_i), len(hyp_embedding_i))
        if len(ref_embedding_i) < max_len:
            ref_embedding_i = np.pad(ref_embedding_i, ((0, max_len - len(ref_embedding_i)), (0, 0)), mode='constant')
        if len(hyp_embedding_i) < max_len:
            hyp_embedding_i = np.pad(hyp_embedding_i, ((0, max_len - len(hyp_embedding_i)), (0, 0)), mode='constant')

        distance_matrix = np.zeros((max_len, max_len))
        for i in range(max_len):
            for j in range(max_len):
                distance_matrix[i][j] = np.linalg.norm(ref_embedding_i[i] - hyp_embedding_i[j])

        max_tokens = max(len(ref_idf), len(hyp_idf))
        ref_idf = np.pad(np.array(ref_idf), (0, max_tokens - len(ref_idf)))
        hyp_idf = np.pad(np.array(hyp_idf), (0, max_tokens - len(hyp_idf)))

        ref_idf = ref_idf / np.sum(ref_idf)
        hyp_idf = hyp_idf / np.sum(hyp_idf)

        score = emd(ref_idf, hyp_idf, distance_matrix)
        scores.append(1 / (1 + score))

    return scores

In [ ]:


# Evaluation metrics
def calculate_metrics(reference, hypothesis):
    rouge = rouge_scorer.RougeScorer(['rouge1', 'rouge2', 'rougeL'], use_stemmer=True)
    rouge_scores = rouge.score(reference, hypothesis)

    bert_precision, bert_recall, bert_f1 = bert_score([hypothesis], [reference], lang="en")

    meteor = meteor_score.meteor_score([reference.split()], hypothesis.split())

    idf_dict_ref = get_idf_dict([reference])
    idf_dict_hyp = get_idf_dict([hypothesis])
    moverscore_value = word_mover_score([reference], [hypothesis], idf_dict_ref, idf_dict_hyp)

    return {
        'ROUGE-1': rouge_scores['rouge1'].fmeasure,
        'ROUGE-2': rouge_scores['rouge2'].fmeasure,
        'ROUGE-L': rouge_scores['rougeL'].fmeasure,
        'METEOR': meteor,
        'BERTScore': bert_f1.item(),
        'Precision': bert_precision.item(),
        'Recall': bert_recall.item(),
        'MoverScore': moverscore_value[0]
    }


In [ ]:
# Move the model to the correct device
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model.to(device)

# Set batch size
batch_size = 8  # Adjust based on your GPU memory

# Generate summaries for the training dataset using batch processing
train_summaries = []

for i in range(0, len(cleaned_injected_train_texts), batch_size):
    batch_texts = cleaned_injected_train_texts[i:i + batch_size]
    batch_retrieved_texts = train_retrieved_texts[i:i + batch_size]

    # Generate summaries for the current batch
    batch_summaries = [generate_summary(text, retrieved_text, model, tokenizer)
                       for text, retrieved_text in zip(batch_texts, batch_retrieved_texts)]
    train_summaries.extend(batch_summaries)  # Add the batch summaries to the main list

# Now, evaluate metrics for the training dataset
train_metrics = [calculate_metrics(reference, summary) for reference, summary in zip(cleaned_train_texts, train_summaries)]

# Generate summaries for the test dataset using batch processing
test_summaries = []

for i in range(0, len(cleaned_injected_test_texts), batch_size):
    batch_texts = cleaned_injected_test_texts[i:i + batch_size]
    batch_retrieved_texts = test_retrieved_texts[i:i + batch_size]

    # Generate summaries for the current batch
    batch_summaries = [generate_summary(text, retrieved_text, model, tokenizer)
                       for text, retrieved_text in zip(batch_texts, batch_retrieved_texts)]
    test_summaries.extend(batch_summaries)  # Add the batch summaries to the main list

# Now, evaluate metrics for the test dataset
test_metrics = [calculate_metrics(reference, summary) for reference, summary in zip(cleaned_test_texts, test_summaries)]


Streaming output truncated to the last 5000 lines.
}

loading weights file model.safetensors from cache at /root/.cache/huggingface/hub/models--roberta-large/snapshots/722cf37b1afa9454edce342e7895e588b6ff1d59/model.safetensors
Some weights of the model checkpoint at roberta-large were not used when initializing RobertaModel: ['lm_head.bias', 'lm_head.dense.bias', 'lm_head.dense.weight', 'lm_head.layer_norm.bias', 'lm_head.layer_norm.weight']
- This IS expected if you are initializing RobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaModel were not initialized from the model checkpoint at roberta-large an

In [ ]:

# Display average metrics for train and test datasets
def display_average_metrics(metrics, dataset_name):
    print(f"\n{dataset_name} Dataset Evaluation:")
    avg_metrics = {metric: np.mean([m[metric] for m in metrics]) for metric in metrics[0].keys()}
    for metric, value in avg_metrics.items():
        print(f"{metric}: {value:.3f}")

display_average_metrics(train_metrics, "Train")
display_average_metrics(test_metrics, "Test")



Train Dataset Evaluation:
ROUGE-1: 0.684
ROUGE-2: 0.596
ROUGE-L: 0.641
METEOR: 0.537
BERTScore: 0.913
Precision: 0.921
Recall: 0.905
MoverScore: 0.241

Test Dataset Evaluation:
ROUGE-1: 0.681
ROUGE-2: 0.612
ROUGE-L: 0.653
METEOR: 0.527
BERTScore: 0.915
Precision: 0.931
Recall: 0.900
MoverScore: 0.258


In [ ]:
# Display original text and summary for the first 10 rows of the test data
print("\nDisplaying the first 10 rows of the test dataset:\n")
for i in range(10):
    print(f"Row {i + 1}:")
    print("Original text:", cleaned_test_texts[i])
    print("Summary:", test_summaries[i])
    print("\n")



Displaying the first 10 rows of the test dataset:

Row 1:
Original text: montague haltrecht was born in willesden north london on 27 february 1932 the third son of immigrant jewish parents his father phillip phil samuelson originally from warsaw in 1904 had come to england in 1922 aged 19 along with his family fleeing from persecution his mother kate oslovski came from a jewish family from poland who had also fled from persecution phil and kate met and married in 1923 and had five children including herbert born in 1931 norman montague and jane and a daughter who died at age 16 edith s father had kept a shoe store harold robinson s in the east end of london which he continued in early life at before moving to golders green in 1942 bill robinson was killed in action in france during the allied invasion in august 1945 while kate haltrecht died august 1946 there phil who found comfort in a friend of his wife s met and married her sometime later phil himself who as a child had been presen

In [ ]:
1 + 1

2

**RAG with T5 2-step summarisation InjectedText at temp 0.7**

In [ ]:


# Set up the device
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')


# Load T5-large tokenizer and model
tokenizer = T5Tokenizer.from_pretrained('t5-large')
model = T5ForConditionalGeneration.from_pretrained('t5-large').to(device)

# Set the number of epochs
num_epochs = 5
train_losses = []

# Training loop with adjustable epochs
optimizer = torch.optim.Adam(model.parameters(), lr=5e-5)

for epoch in range(num_epochs):
    print(f"Epoch {epoch + 1}/{num_epochs}")

    model.train()
    epoch_train_loss = 0

    for i in range(0, len(cleaned_injected_train_texts), 4):  # Batch size of 4
        batch_texts = cleaned_injected_train_texts[i:i+4]
        batch_retrieved_texts = train_retrieved_texts[i:i+4]
        input_texts = [f"Perform abstractive summarization: {text}" for text in batch_texts]

        # Check if input_texts is empty
        if not input_texts:
            raise ValueError("Input texts are empty.")

        # Print input texts for debugging
        print("Input texts:", input_texts)

        inputs = tokenizer(input_texts, return_tensors='pt', padding=True, truncation=True, max_length=512).to(device)
        label_max_length = int(0.5 * inputs['input_ids'].size(1))
        labels = tokenizer(batch_texts, return_tensors='pt', padding=True, truncation=True, max_length=label_max_length)['input_ids'].to(device)

        outputs = model(input_ids=inputs['input_ids'], attention_mask=inputs['attention_mask'], labels=labels)
        loss = outputs.loss

        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        epoch_train_loss += loss.item()

    avg_train_loss = epoch_train_loss / len(cleaned_injected_train_texts)
    train_losses.append(avg_train_loss)
    print(f"Training Loss: {avg_train_loss:.3f}")

    gc.collect()
    torch.cuda.empty_cache()

loading file spiece.model from cache at /root/.cache/huggingface/hub/models--t5-large/snapshots/150ebc2c4b72291e770f58e6057481c8d2ed331a/spiece.model
loading file added_tokens.json from cache at None
loading file special_tokens_map.json from cache at None
loading file tokenizer_config.json from cache at None
loading file tokenizer.json from cache at /root/.cache/huggingface/hub/models--t5-large/snapshots/150ebc2c4b72291e770f58e6057481c8d2ed331a/tokenizer.json
loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--t5-large/snapshots/150ebc2c4b72291e770f58e6057481c8d2ed331a/config.json
Model config T5Config {
  "_name_or_path": "t5-large",
  "architectures": [
    "T5ForConditionalGeneration"
  ],
  "classifier_dropout": 0.0,
  "d_ff": 4096,
  "d_kv": 64,
  "d_model": 1024,
  "decoder_start_token_id": 0,
  "dense_act_fn": "relu",
  "dropout_rate": 0.1,
  "eos_token_id": 1,
  "feed_forward_proj": "relu",
  "initializer_factor": 1.0,
  "is_encoder_decoder

Epoch 1/5
Input texts: ['Perform abstractive summarization: christopher atkinson c 1738 23 april 1819 known as christopher atkinson savile or saville from about 1798 was an english merchant and politician the river styx forms the boundary between earth and the underworld born in yorkshire he moved to dorset and married the niece of a wealthy merchant entering that business himself he was elected at the 1780 general election as one of the two members of parliament mps for dorset west however he was expelled from the house of commons on the second sitting after being convicted of receiving a bribe and sentenced to detention in the pillory he was granted a royal warrant in 1791 and returned to parliament for the area in 1796 retaining the seat until he stood down at the 1802 general election he had changed his name to atkinson atkinson some time after 1793 hades realm is called the underworld or hades itself he then purchased extensive estates in westerleigh in hampshire which gave him co

In [ ]:
import re
import torch

def complete_last_sentence(text):
    sentences = re.split('(?<=[.!?]) +', text)
    if len(sentences) > 1:
        if len(sentences[-1].split()) < 3:
            text = ' '.join(sentences[:-1])
        else:
            if not sentences[-1][-1] in '.!?':
                text = text + '.'
    else:
        if not text[-1] in '.!?':
            text = text + '.'
    return text

def generate_summary(text, retrieved_texts, model, tokenizer, device):
    text = complete_last_sentence(text)
    input_text = f"Refine the following summary using this additional context. Text: {text} Additional context: {' '.join(retrieved_texts)}"
    inputs = tokenizer.encode(input_text, return_tensors='pt', max_length=512, truncation=True).to(device)

    decoder_settings = {
        "no_repeat_ngram_size": 2,
        "max_length": int(0.5 * inputs.size(1)),
        "min_length": int(0.25 * inputs.size(1)),
        "length_penalty": 2.5,
        "temperature": 0.7,
        "top_p": 0.9,
        "top_k": 50,
        "num_beams": 5,
        "do_sample": True,
        "early_stopping": True
    }

    summary_ids = model.generate(inputs, **decoder_settings)
    final_summary = tokenizer.decode(summary_ids[0], skip_special_tokens=True)

    if not final_summary.endswith('.'):
        final_summary += '.'

    return final_summary


In [ ]:
# Initialize BERT model for evaluation
bert_tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
bert_model = BertModel.from_pretrained('bert-base-uncased')
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
bert_model.to(device)

def bert_encode(model, x, device='cpu'):
    model.eval()
    with torch.no_grad():
        x = [bert_tokenizer.encode(sent, add_special_tokens=True) for sent in x]
        x = torch.tensor(x).to(device)
        outputs = model(x)
        return outputs.last_hidden_state

loading file vocab.txt from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/vocab.txt
loading file added_tokens.json from cache at None
loading file special_tokens_map.json from cache at None
loading file tokenizer_config.json from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/tokenizer_config.json
loading file tokenizer.json from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/tokenizer.json
loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--bert-base-uncased/snapshots/86b5e0934494bd15c9632b12f734a8a67f723594/config.json
Model config BertConfig {
  "_name_or_path": "bert-base-uncased",
  "architectures": [
    "BertForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "classifier_dropout": null,
  "gradient_checkpointing": false,
  "hidden_ac

In [ ]:




def word_mover_score(references, hypotheses, idf_dict_ref, idf_dict_hyp, stop_words=None, n_gram=1, remove_subwords=True):
    if stop_words is None:
        stop_words = []

    ref_embedding = bert_encode(bert_model.to(device), references, device)
    hyp_embedding = bert_encode(bert_model.to(device), hypotheses, device)

    ref_embedding = ref_embedding.cpu().numpy()
    hyp_embedding = hyp_embedding.cpu().numpy()

    scores = []
    for i in range(len(references)):
        ref_tokens = references[i].split()
        hyp_tokens = hypotheses[i].split()

        ref_idf = [idf_dict_ref[token] for token in ref_tokens if token not in stop_words]
        hyp_idf = [idf_dict_hyp[token] for token in hyp_tokens if token not in stop_words]

        ref_embedding_i = ref_embedding[i]
        hyp_embedding_i = hyp_embedding[i]

        max_len = max(len(ref_embedding_i), len(hyp_embedding_i))
        if len(ref_embedding_i) < max_len:
            ref_embedding_i = np.pad(ref_embedding_i, ((0, max_len - len(ref_embedding_i)), (0, 0)), mode='constant')
        if len(hyp_embedding_i) < max_len:
            hyp_embedding_i = np.pad(hyp_embedding_i, ((0, max_len - len(hyp_embedding_i)), (0, 0)), mode='constant')

        distance_matrix = np.zeros((max_len, max_len))
        for i in range(max_len):
            for j in range(max_len):
                distance_matrix[i][j] = np.linalg.norm(ref_embedding_i[i] - hyp_embedding_i[j])

        max_tokens = max(len(ref_idf), len(hyp_idf))
        ref_idf = np.pad(np.array(ref_idf), (0, max_tokens - len(ref_idf)))
        hyp_idf = np.pad(np.array(hyp_idf), (0, max_tokens - len(hyp_idf)))

        ref_idf = ref_idf / np.sum(ref_idf)
        hyp_idf = hyp_idf / np.sum(hyp_idf)

        score = emd(ref_idf, hyp_idf, distance_matrix)
        scores.append(1 / (1 + score))

    return scores

In [ ]:


# Evaluation metrics
def calculate_metrics(reference, hypothesis):
    rouge = rouge_scorer.RougeScorer(['rouge1', 'rouge2', 'rougeL'], use_stemmer=True)
    rouge_scores = rouge.score(reference, hypothesis)

    bert_precision, bert_recall, bert_f1 = bert_score([hypothesis], [reference], lang="en")

    meteor = meteor_score.meteor_score([reference.split()], hypothesis.split())

    idf_dict_ref = get_idf_dict([reference])
    idf_dict_hyp = get_idf_dict([hypothesis])
    moverscore_value = word_mover_score([reference], [hypothesis], idf_dict_ref, idf_dict_hyp)

    return {
        'ROUGE-1': rouge_scores['rouge1'].fmeasure,
        'ROUGE-2': rouge_scores['rouge2'].fmeasure,
        'ROUGE-L': rouge_scores['rougeL'].fmeasure,
        'METEOR': meteor,
        'BERTScore': bert_f1.item(),
        'Precision': bert_precision.item(),
        'Recall': bert_recall.item(),
        'MoverScore': moverscore_value[0]
    }


In [ ]:
import torch

# Move the model to the correct device
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model.to(device)

# Set batch size
batch_size = 8

# Generate summaries for the training dataset using batch processing
train_intermediate_summaries = []
train_final_summaries = []

for i in range(0, len(cleaned_injected_train_texts), batch_size):
    batch_texts = cleaned_injected_train_texts[i:i + batch_size]
    batch_retrieved_texts = train_retrieved_texts[i:i + batch_size]

    # Step 1: Generate intermediate summaries for the current batch
    intermediate_summaries = [generate_summary(text, retrieved_text, model, tokenizer, device)
                               for text, retrieved_text in zip(batch_texts, batch_retrieved_texts)]
    train_intermediate_summaries.extend(intermediate_summaries)  # Store intermediate summaries

    # Step 2: Generate final summaries from the intermediate summaries
    final_summaries = [generate_summary(intermediate, [], model, tokenizer, device)
                       for intermediate in intermediate_summaries]  # Assuming no additional context for final summaries
    train_final_summaries.extend(final_summaries)  # Store final summaries

# Now, evaluate metrics for the training dataset
train_metrics = [calculate_metrics(reference, summary) for reference, summary in zip(cleaned_train_texts, train_final_summaries)]

# Generate summaries for the test dataset using batch processing
test_intermediate_summaries = []
test_final_summaries = []

for i in range(0, len(cleaned_injected_test_texts), batch_size):
    batch_texts = cleaned_injected_test_texts[i:i + batch_size]
    batch_retrieved_texts = test_retrieved_texts[i:i + batch_size]

    # Step 1: Generate intermediate summaries for the current batch
    intermediate_summaries = [generate_summary(text, retrieved_text, model, tokenizer, device)
                               for text, retrieved_text in zip(batch_texts, batch_retrieved_texts)]
    test_intermediate_summaries.extend(intermediate_summaries)  # Store intermediate summaries

    # Step 2: Generate final summaries from the intermediate summaries
    final_summaries = [generate_summary(intermediate, [], model, tokenizer, device)
                       for intermediate in intermediate_summaries]  # Assuming no additional context for final summaries
    test_final_summaries.extend(final_summaries)  # Store final summaries

# Now, evaluate metrics for the test dataset
test_metrics = [calculate_metrics(reference, summary) for reference, summary in zip(cleaned_test_texts, test_final_summaries)]


Streaming output truncated to the last 5000 lines.
}

loading weights file model.safetensors from cache at /root/.cache/huggingface/hub/models--roberta-large/snapshots/722cf37b1afa9454edce342e7895e588b6ff1d59/model.safetensors
Some weights of the model checkpoint at roberta-large were not used when initializing RobertaModel: ['lm_head.bias', 'lm_head.dense.bias', 'lm_head.dense.weight', 'lm_head.layer_norm.bias', 'lm_head.layer_norm.weight']
- This IS expected if you are initializing RobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaModel were not initialized from the model checkpoint at roberta-large an

In [ ]:

# Display average metrics for train and test datasets
def display_average_metrics(metrics, dataset_name):
    print(f"\n{dataset_name} Dataset Evaluation:")
    avg_metrics = {metric: np.mean([m[metric] for m in metrics]) for metric in metrics[0].keys()}
    for metric, value in avg_metrics.items():
        print(f"{metric}: {value:.3f}")

display_average_metrics(train_metrics, "Train")
display_average_metrics(test_metrics, "Test")



Train Dataset Evaluation:
ROUGE-1: 0.477
ROUGE-2: 0.421
ROUGE-L: 0.454
METEOR: 0.292
BERTScore: 0.888
Precision: 0.921
Recall: 0.858
MoverScore: 0.110

Test Dataset Evaluation:
ROUGE-1: 0.481
ROUGE-2: 0.454
ROUGE-L: 0.472
METEOR: 0.296
BERTScore: 0.898
Precision: 0.939
Recall: 0.860
MoverScore: 0.103


In [ ]:
# Display original text and summary for the first 10 rows of the test data
print("\nDisplaying the first 10 rows of the test dataset:\n")
for i in range(10):
    print(f"Row {i + 1}:")
    print("Original text:", cleaned_test_texts[i])
    print("Summary:", test_summaries[i])
    print("\n")


Displaying the first 10 rows of the test dataset:

Row 1:
Original text: montague haltrecht was born in willesden north london on 27 february 1932 the third son of immigrant jewish parents his father phillip phil samuelson originally from warsaw in 1904 had come to england in 1922 aged 19 along with his family fleeing from persecution his mother kate oslovski came from a jewish family from poland who had also fled from persecution phil and kate met and married in 1923 and had five children including herbert born in 1931 norman montague and jane and a daughter who died at age 16 edith s father had kept a shoe store harold robinson s in the east end of london which he continued in early life at before moving to golders green in 1942 bill robinson was killed in action in france during the allied invasion in august 1945 while kate haltrecht died august 1946 there phil who found comfort in a friend of his wife s met and married her sometime later phil himself who as a child had been presen

In [ ]:
!cat /usr/local/lib/python3.10/dist-packages/moverscore_v2.py

from __future__ import absolute_import, division, print_function
import numpy as np
import torch
import string
from pyemd import emd, emd_with_flow
from torch import nn
from math import log
from itertools import chain

from collections import defaultdict, Counter
from multiprocessing import Pool
from functools import partial


from transformers import *
model_name = 'distilbert-base-uncased'
device = 'cuda:0'
config = DistilBertConfig.from_pretrained(model_name, output_hidden_states=True, output_attentions=True)
tokenizer = DistilBertTokenizer.from_pretrained(model_name, do_lower_case=True)
model = DistilBertModel.from_pretrained(model_name, config=config)
model.eval()
model.to(device) 
                
def truncate(tokens):
    if len(tokens) > tokenizer.model_max_length - 2:
        tokens = tokens[0:(tokenizer.model_max_length - 2)]
    return tokens

def process(a):
    a = ["[CLS]"]+truncate(tokenizer.tokenize(a))+["[SEP]"]
    a = tokenizer.convert_tokens_to_ids(a)
    return set

In [ ]:
!cp /usr/local/lib/python3.10/dist-packages/moverscore_v2.py ./moverscore_v2_modified.py


In [ ]:
from google.colab import files
files.view('./moverscore_v2_modified.py')

<IPython.core.display.Javascript object>

In [ ]:
!cp ./moverscore_v2_modified.py /usr/local/lib/python3.10/dist-packages/moverscore_v2.py

In [ ]:
!cat /usr/local/lib/python3.10/dist-packages/moverscore_v2.py | grep "model_max_length"

    if len(tokens) > tokenizer.model_max_length - 2:
        tokens = tokens[0:(tokenizer.model_max_length - 2)]
